In [2]:
####################### AUTO LOGIN #####################
import os
os.system('clear')
import warnings
warnings.filterwarnings("ignore", category=RuntimeWarning) 
print('Starting Strategy...')
import json
import login
from login import *
import pandas as pd
import joblib
import ta
import requests
import numpy as np
pd.set_option('plotting.backend', 'pandas_bokeh')
import pandas_bokeh
pandas_bokeh.output_notebook()
import h2o
hh=h2o.init(ip='127.0.0.1',port='12349')
n50 = pd.read_csv('n50.csv')
nfifty_tokens_list = n50['instrument_token'].to_numpy().tolist()
n100 = pd.read_csv('n100.csv')
n100_tokens_list = n100['instrument_token'].to_numpy().tolist()

Starting Strategy...
access token : 5ISvHh624SAR9CsFQMTjmivTsBmebc78
request token : 7CcsfhWO3GNV5UyLktqhTpTrOgSuxF1y


Loading BokehJS ...

Checking whether there is an H2O instance running at http://127.0.0.1:12349 ..... not found.
Attempting to start a local H2O server...
  Java Version: openjdk version "14.0.2" 2020-07-14; OpenJDK Runtime Environment (build 14.0.2+12-Ubuntu-2); OpenJDK 64-Bit Server VM (build 14.0.2+12-Ubuntu-2, mixed mode, sharing)
  Starting server from /home/hemang/.local/lib/python3.9/site-packages/h2o/backend/bin/h2o.jar
  Ice root: /tmp/tmp_uojjxb7
  JVM stdout: /tmp/tmp_uojjxb7/h2o_hemang_started_from_python.out
  JVM stderr: /tmp/tmp_uojjxb7/h2o_hemang_started_from_python.err
  Server is running at http://127.0.0.1:12351
Connecting to H2O server at http://127.0.0.1:12351 ... successful.


--------------------------  ------------------------------------------------------------------
H2O_cluster_uptime:         02 secs
H2O_cluster_timezone:       Asia/Kolkata
H2O_data_parsing_timezone:  UTC
H2O_cluster_version:        3.32.0.3
H2O_cluster_version_age:    22 days
H2O_cluster_name:           H2O_from_python_hemang_b1sroa
H2O_cluster_total_nodes:    1
H2O_cluster_free_memory:    1.848 Gb
H2O_cluster_total_cores:    8
H2O_cluster_allowed_cores:  8
H2O_cluster_status:         accepting new members, healthy
H2O_connection_url:         http://127.0.0.1:12351
H2O_connection_proxy:       {"http": null, "https": null}
H2O_internal_security:      False
H2O_API_Extensions:         Amazon S3, XGBoost, Algos, AutoML, Core V3, TargetEncoder, Core V4
Python_version:             3.9.1 final
--------------------------  ------------------------------------------------------------------

In [1]:
all_inst = kite.instrument()

NameError: name 'kite' is not defined

In [3]:
order_type = 'MIS' 
mymargin = 5000
interval='5minute'
daysdiff = 5
bkg = 0.0
isneg = 1

todaydt=datetime.date.today()
hud_ago=todaydt-datetime.timedelta(days=daysdiff)
to_date=datetime.date.isoformat(todaydt)
from_date=datetime.date.isoformat(hud_ago)

In [4]:
# one stock predict and place order

saved_model = h2o.load_model('./model1')
saved_model2 = h2o.load_model('./model2')
saved_model3 = h2o.load_model('./model3')
saved_model4 = h2o.load_model('../GBM_3_AutoML_20210113_220248')

def one_stk_fun(insttkn,tradeon=False):
    '''one_stk_fun(insttkn,tradeon=False)'''

    old_lst = kite.historical_data(insttkn, from_date, to_date, interval,continuous=False)

    mydf = pd.DataFrame(old_lst)
    mydf = mydf.fillna(0)
    mydf = ta.add_all_ta_features(mydf, open="open", high="high", low="low", close="close", volume="volume")
    mydf = mydf.fillna(0)[150:]
    
    hf = h2o.H2OFrame(mydf)

    prd1 = saved_model.predict(hf)
    ct1 = prd1.concat([hf])
    prd2 = saved_model2.predict(ct1)
    ct2 = prd2.concat([ct1])
    prd3 = saved_model.predict(ct2)
    ct3 = prd3.concat([ct2])
    prd4 = saved_model2.predict(ct3)
    ct4 = prd4.concat([ct3])

    os.system('clear')
    data_as_df = h2o.as_list(ct4)  

    sel_data = data_as_df[['predict','predict0','predict0.1','date','close']] #,'next_close'

    last_isbullbear = 0

    total_gained_pt = []
    total_gained_pt_total = 0
    total_gained_pt_lst = []

    for ind in sel_data.index:
        
        is_bullbear = 0

        if(ind<(len(sel_data.index)-1)):
            if(sel_data['close'][ind]<sel_data['close'][ind+1]):
                is_bullbear=1
            elif(sel_data['close'][ind]>sel_data['close'][ind+1]):
                is_bullbear=-1

        pred_bullbear = 0
    
        if(ind<(len(sel_data.index)-1)):
            if(sel_data['predict'][ind]<sel_data['close'][ind]):
                pred_bullbear=-1
            elif(sel_data['predict'][ind]>sel_data['close'][ind]):
                pred_bullbear=1

        pred_true = -1

        if(pred_bullbear==is_bullbear):
            pred_true = 1

        gained_pt=0
        if(ind<(len(sel_data.index)-1)):
            gained_pt = pred_true*abs(sel_data['close'][ind]-sel_data['close'][ind+1])

        gained_pt = gained_pt*isneg
        if(ind>0 and (last_isbullbear!=is_bullbear)):
            gained_pt = gained_pt+bkg

        total_gained_pt.append(gained_pt)
        total_gained_pt_total = total_gained_pt_total + gained_pt
        total_gained_pt_lst.append(total_gained_pt_total)
        last_isbullbear = is_bullbear
    
    this_mean_val = np.array(total_gained_pt_lst).mean()
    gdptdf = pd.DataFrame({'total_gained_pt':total_gained_pt,'total_gained_pt_lst':total_gained_pt_lst})
#     gdptdf.plot()
    
    pred_close = data_as_df.iloc[[-1]]['predict'].to_numpy()[0]
    this_close = data_as_df.iloc[[-1]]['close'].to_numpy()[0]
    
    this_mean_percent = (this_mean_val/this_close)*100

    current_bullbear = 0

    if(pred_close>this_close):
        current_bullbear=1

    elif(pred_close<this_close):
        current_bullbear=-1

    print('=============================')
    print('current_bullbear : '+str(current_bullbear))
    print('pred_close : '+str(pred_close))
    print('this_close : '+str(this_close))
    print('this_mean_percent : '+str(this_mean_percent))
    print(data_as_df.iloc[[-1]]['date'].to_numpy()[0])
    print('=============================')

    if(tradeon):
        ckqnt(0,current_bullbear*full_qty)

    globals()['df'+str(insttkn)] = pd.DataFrame({insttkn:total_gained_pt_lst})
    globals()['df'+str(insttkn)] = (globals()['df'+str(insttkn)]/this_close)*100
    return globals()['df'+str(insttkn)]

In [14]:
# Select Target Token and Symbol Name
def decide_target(nfifty_tokens_list):
    global mynp,last_mean
    '''decide_target(nfifty_tokens_list)'''
    combined_df = pd.DataFrame()
    counter1 = 1
    for iii in nfifty_tokens_list:
        
        symbol_name1 = n100.loc[n100['instrument_token'] == iii, 'tradingsymbol'].to_numpy()[0]
        print()
        print('============================================================================')
        print('Analyzing Token : '+str(iii)+ ' : '+str(symbol_name1)+ ' : '+str(counter1)+'/50')
        print('============================================================================')
        counter1 = counter1+1
        one_stk_fun(iii,tradeon=False)
        combined_df = pd.concat([combined_df,globals()['df'+str(iii)]], axis=1)

    combined_df.plot()
    os.system('clear')
    
    
    mynp = combined_df.iloc[[-1]].to_numpy()[0]
    mynp = np.nan_to_num(mynp)
    print('Nifty50 Mean : '+str(np.mean(mynp)))
    print('Nifty50 Sum : '+str(np.sum(mynp)))

    insttkn = 0
    last_mean = 0

    for ij in range(len(nfifty_tokens_list)):
        this_mean = combined_df[nfifty_tokens_list[ij]].to_numpy().mean()

        if(this_mean>last_mean):
            insttkn= nfifty_tokens_list[ij]
            last_mean = this_mean


    symbol_ip = n100.loc[n100['instrument_token'] == insttkn, 'tradingsymbol'].to_numpy()[0]

    print('Success Rate Mean : '+str(last_mean))
    print('Selected Token : '+str(insttkn))
    print('Selected Symbol : '+str(symbol_ip))
    return {'insttkn':insttkn,'symbol_ip':symbol_ip,'mean':last_mean}

In [6]:
# base functions : getquant, placeneworder, ckqnt

myquantity = 0
def getquant():
    global myquantity,order_type,symbol_ip
    allpos = kite.positions()['net']
    for i in range(len(allpos)):
        if(allpos[i]['tradingsymbol']==symbol_ip and  allpos[i]['product']== order_type):
            myquantity = allpos[i]['quantity']
            print('My Quantity : ' + str(allpos[i]['quantity']))


stop_trading = False
stopbuy = False
stopsell = False
ex_type = kite.EXCHANGE_NSE

def placeneworder(quantdiff,price_ip):
    global stopbuy,stop_trading,stopsell,order_type,symbol_ip,ex_type
    if(quantdiff>0 and stopbuy == False and stop_trading==False):
        try:
            stop_trading = True
            order_id= kite.place_order(tradingsymbol=symbol_ip,
                        exchange=ex_type,
                        transaction_type=kite.TRANSACTION_TYPE_BUY,
                        quantity=abs(quantdiff),
#                             price=price_ip,
                        order_type=kite.ORDER_TYPE_MARKET,
                        variety = kite.VARIETY_REGULAR,
                        product=kite.PRODUCT_MIS if order_type=='MIS' else kite.PRODUCT_NRML)
            getquant()
            stopsell = False
            stop_trading = False
        except Exception as e:
#             stopbuy = True
            print(e)
            getquant()
    if(quantdiff<0 and stopsell == False and stop_trading==False):
        try:
            stop_trading = True
            order_id= kite.place_order(tradingsymbol=symbol_ip,
                        exchange=ex_type,
                        transaction_type=kite.TRANSACTION_TYPE_SELL,
                        quantity=abs(quantdiff),
#                             price=price_ip,
                        order_type=kite.ORDER_TYPE_MARKET,
                        variety = kite.VARIETY_REGULAR,
                        product=kite.PRODUCT_MIS if order_type=='MIS' else kite.PRODUCT_NRML)
            getquant()
            stopbuy = False
            stop_trading = False
        except Exception as e:
#             stopsell = True
            print(e)
            getquant()

def ckqnt (orderprice,orderquant):
    global myquantity
    quantdiff = orderquant - myquantity
    placeneworder(quantdiff,orderprice)
    return myquantity

def print_params():
    print('=============================')
    print('Nifty50 Mean : '+str(np.mean(mynp)))
    print('Nifty50 Sum : '+str(np.sum(mynp)))
    print('Success Rate Mean : '+str(last_mean))
    print('Selected Token : '+str(insttkn))
    print('Selected Symbol : '+str(symbol_ip))
    print('Order Type : '+str(order_type))
    print('My Margin : '+str(mymargin))
    print('Interval : '+str(interval))
    print('MIS Qty : '+str(full_qty))
    print('=============================')

In [15]:
############### Calculate MIS Qty ############

url = 'https://api.kite.trade/margins/equity'
margin_data = requests.get(url, timeout=2.50)
margin_map = json.loads(margin_data.content.decode('utf-8'))
margin_map_df = pd.DataFrame(margin_map)
margin_map_df

ipmap = decide_target(nfifty_tokens_list)

symbol_ip = ipmap['symbol_ip']
insttkn = ipmap['insttkn']

mis_margin = margin_map_df.loc[margin_map_df['tradingsymbol'] == symbol_ip, 'mis_multiplier'].to_numpy()[0]

myqt = kite.quote([insttkn])
ltp = myqt[str(insttkn)]['last_price']
mis_margin_ip = ltp/mis_margin

full_qty = int(mymargin/mis_margin_ip)
full_qty


Analyzing Token : 3861249 : ADANIPORTS : 1/50
Parse progress: |█████████████████████████████████████████████████████████| 100%
xgboost prediction progress: |████████████████████████████████████████████| 100%
gbm prediction progress: |████████████████████████████████████████████████| 100%
xgboost prediction progress: |████████████████████████████████████████████| 100%
gbm prediction progress: |████████████████████████████████████████████████| 100%
current_bullbear : 1
pred_close : 536.748780736245
this_close : 536.15
this_mean_percent : -2.7255889271868816
2021-01-15 09:15:00+05:30

Analyzing Token : 60417 : ASIANPAINT : 2/50
Parse progress: |█████████████████████████████████████████████████████████| 100%
xgboost prediction progress: |████████████████████████████████████████████| 100%
gbm prediction progress: |████████████████████████████████████████████████| 100%
xgboost prediction progress: |████████████████████████████████████████████| 100%
gbm prediction progress: |████████████████

xgboost prediction progress: |████████████████████████████████████████████| 100%
gbm prediction progress: |████████████████████████████████████████████████| 100%
xgboost prediction progress: |████████████████████████████████████████████| 100%
gbm prediction progress: |████████████████████████████████████████████████| 100%
current_bullbear : -1
pred_close : 3257.7583230511627
this_close : 3257.95
this_mean_percent : 0.8980274334539449
2021-01-15 09:15:00+05:30

Analyzing Token : 348929 : HINDALCO : 22/50
Parse progress: |█████████████████████████████████████████████████████████| 100%
xgboost prediction progress: |████████████████████████████████████████████| 100%
gbm prediction progress: |████████████████████████████████████████████████| 100%
xgboost prediction progress: |████████████████████████████████████████████| 100%
gbm prediction progress: |████████████████████████████████████████████████| 100%
current_bullbear : 1
pred_close : 262.4152057154388
this_close : 262.35
this_mean_perc

current_bullbear : -1
pred_close : 23965.96238613677
this_close : 24686.9
this_mean_percent : 2.5856569396982163
2021-01-15 09:15:00+05:30

Analyzing Token : 857857 : SUNPHARMA : 42/50
Parse progress: |█████████████████████████████████████████████████████████| 100%
xgboost prediction progress: |████████████████████████████████████████████| 100%
gbm prediction progress: |████████████████████████████████████████████████| 100%
xgboost prediction progress: |████████████████████████████████████████████| 100%
gbm prediction progress: |████████████████████████████████████████████████| 100%
current_bullbear : 1
pred_close : 607.848232354514
this_close : 607.3
this_mean_percent : -0.3996082977199128
2021-01-15 09:15:00+05:30

Analyzing Token : 884737 : TATAMOTORS : 43/50
Parse progress: |█████████████████████████████████████████████████████████| 100%
xgboost prediction progress: |████████████████████████████████████████████| 100%
gbm prediction progress: |███████████████████████████████████████

Nifty50 Mean : 0.1239267546582675
Nifty50 Sum : 6.196337732913375
Success Rate Mean : 3.350254599875243
Selected Token : 81153
Selected Symbol : BAJFINANCE


8

In [16]:
# 5 minute time loop with predict/order Fn
import time
last_min = 0
getquant()

while(1):
    minute=datetime.datetime.now().minute
    if(minute%5==0 and(minute!=last_min)):
        os.system('clear')
        one_stk_fun(insttkn)
        print_params()
        last_min=minute
    time.sleep(0.1)

Parse progress: |█████████████████████████████████████████████████████████| 100%
xgboost prediction progress: |████████████████████████████████████████████| 100%
gbm prediction progress: |████████████████████████████████████████████████| 100%
xgboost prediction progress: |████████████████████████████████████████████| 100%
gbm prediction progress: |████████████████████████████████████████████████| 100%
current_bullbear : -1
pred_close : 4891.464072957762
this_close : 4895.45
this_mean_percent : 3.3477716418737313
2021-01-15 09:20:00+05:30
Nifty50 Mean : 0.1239267546582675
Nifty50 Sum : 6.196337732913375
Success Rate Mean : 3.350254599875243
Selected Token : 81153
Selected Symbol : BAJFINANCE
Order Type : MIS
My Margin : 5000
Interval : 5minute
MIS Qty : 8


KeyboardInterrupt: 

In [ ]:
one_stk_fun(1270529,tradeon=False)
# 969473
# 81153

In [ ]:
# import py_compile
# py_compile.compile('./mystrat.py')

In [ ]:
# ipynb-py-convert stock_predict_pipe_11_1_2021.ipynb mystrat.py
# python3 -m compileall mystrat.py

In [ ]:
for i in range(5):
    
    todaydt=datetime.date.today()-datetime.timedelta(days=i*5)
    hud_ago=todaydt-datetime.timedelta(days=4)
    to_proloss_date=datetime.date.isoformat(todaydt)
    from_proloss_date=datetime.date.isoformat(hud_ago)
    print('to_proloss_date '+str(to_proloss_date))
    print('from_proloss_date '+str(from_proloss_date))
    
    
######################################    

    todaydt=datetime.date.today()-datetime.timedelta(days=(i+1)*5)
    hud_ago=todaydt-datetime.timedelta(days=4)
    to_calc_taget_date=datetime.date.isoformat(todaydt)
    from_calc_taget_date=datetime.date.isoformat(hud_ago)
    print('to_calc_taget_date '+str(to_calc_taget_date))
    print('from_calc_taget_date '+str(from_calc_taget_date))
    
################################    

    
    to_date = to_calc_taget_date
    from_date = from_calc_taget_date
    map1 = decide_target(nfifty_tokens_list)
    
#################################

    to_date = to_proloss_date
    from_date = from_proloss_date
    
    tknip = map1['insttkn']
    print('*********************************************')
    one_stk_fun(tknip,False)
    print('*********************************************')
    
    print()    

In [ ]:
# Datetime features

# df[‘ScheduledDay_year’] = df[‘ScheduledDay’].dt.year
# df[‘ScheduledDay_month’] = df[‘ScheduledDay’].dt.month
# df[‘ScheduledDay_week’] = df[‘ScheduledDay’].dt.week
# df[‘ScheduledDay_day’] = df[‘ScheduledDay’].dt.day
# df[‘ScheduledDay_hour’] = df[‘ScheduledDay’].dt.hour
# df[‘ScheduledDay_minute’] = df[‘ScheduledDay’].dt.minute
# df[‘ScheduledDay_dayofweek’] = df[‘ScheduledDay’].dt.dayofweek

# pandas.Series.asfreq
# pandas.Series.asof
# pandas.Series.shift
# pandas.Series.first_valid_index
# pandas.Series.last_valid_index
# pandas.Series.resample
# pandas.Series.tz_convert
# pandas.Series.tz_localize
# pandas.Series.at_time
# pandas.Series.between_time
# pandas.Series.tshift
# pandas.Series.slice_shift

# pandas.Series.dt.date
# pandas.Series.dt.time
# pandas.Series.dt.year
# pandas.Series.dt.month
# pandas.Series.dt.day
# pandas.Series.dt.hour
# pandas.Series.dt.minute
# pandas.Series.dt.second
# pandas.Series.dt.microsecond
# pandas.Series.dt.nanosecond
# pandas.Series.dt.week
# pandas.Series.dt.weekofyear
# pandas.Series.dt.dayofweek
# pandas.Series.dt.weekday
# pandas.Series.dt.dayofyear
# pandas.Series.dt.quarter
# pandas.Series.dt.is_month_start
# pandas.Series.dt.is_month_end
# pandas.Series.dt.is_quarter_start
# pandas.Series.dt.is_quarter_end
# pandas.Series.dt.is_year_start
# pandas.Series.dt.is_year_end
# pandas.Series.dt.is_leap_year
# pandas.Series.dt.daysinmonth
# pandas.Series.dt.days_in_month
# pandas.Series.dt.tz
# pandas.Series.dt.freq
# pandas.Series.dt.to_period
# pandas.Series.dt.to_pydatetime
# pandas.Series.dt.tz_localize
# pandas.Series.dt.tz_convert
# pandas.Series.dt.normalize
# pandas.Series.dt.strftime
# pandas.Series.dt.round
# pandas.Series.dt.floor
# pandas.Series.dt.ceil
# pandas.Series.dt.month_name
# pandas.Series.dt.day_name
# pandas.Series.dt.days
# pandas.Series.dt.seconds
# pandas.Series.dt.microseconds
# pandas.Series.dt.nanoseconds
# pandas.Series.dt.components
# pandas.Series.dt.to_pytimedelta
# pandas.Series.dt.total_seconds